# Project 2: Web Traffic Analysis
**This is the second of three mandatory projects to be handed in as part of the assessment for the course 02807 Computational Tools for Data Science at Technical University of Denmark, autumn 2019.**

#### Practical info
- **The project is to be done in groups of at most 3 students**
- **Each group has to hand in _one_ Jupyter notebook (this notebook) with their solution**
- **The hand-in of the notebook is due 2019-11-10, 23:59 on DTU Inside**

#### Your solution
- **Your solution should be in Python**
- **For each question you may use as many cells for your solution as you like**
- **You should document your solution and explain the choices you've made (for example by using multiple cells and use Markdown to assist the reader of the notebook)**
- **You should not remove the problem statements**
- **Your notebook should be runnable, i.e., clicking [>>] in Jupyter should generate the result that you want to be assessed**
- **You are not expected to use machine learning to solve any of the exercises**
- **You will be assessed according to correctness and readability of your code, choice of solution, choice of tools and libraries, and documentation of your solution**

## Introduction
In this project your task is to analyze a stream of log entries. A log entry consists of an [IP address](https://en.wikipedia.org/wiki/IP_address) and a [domain name](https://en.wikipedia.org/wiki/Domain_name). For example, a log line may look as follows:

`192.168.0.1 somedomain.dk`

One log line is the result of the event that the domain name was visited by someone having the corresponding IP address. Your task is to analyze the traffic on a number of domains. Counting the number of unique IPs seen on a domain doesn't correspond to the exact number of unique visitors, but it is a good estimate.

Specifically, you should answer the following questions from the stream of log entries.

- How many unique IPs are there in the stream?
- How many unique IPs are there for each domain?
- How many times was IP X seen on domain Y? (for some X and Y provided at run time)

**The answers to these questions can be approximate!**

You should also try to answer one or more of the following, more advanced, questions. The answers to these should also be approximate.

- How many unique IPs are there for the domains $d_1, d_2, \ldots$?
- How many times was IP X seen on domains $d_1, d_2, \ldots$?
- What are the X most frequent IPs in the stream?

You should use algorithms and data structures that you've learned about in the lectures, and you should provide your own implementations of these.

Furthermore, you are expected to:

- Document the accuracy of your answers when using algorithms that give approximate answers
- Argue why you are using certain parameters for your data structures

This notebook is in three parts. In the first part you are given an example of how to read from the stream (which for the purpose of this project is a remote file). In the second part you should implement the algorithms and data structures that you intend to use, and in the last part you should use these for analyzing the stream.

## Reading the stream
The following code reads a remote file line by line. It is wrapped in a generator to make it easier to extend. You may modify this if you want to, but your solution should remain parametrized, so that your notebook can be run without having to consume the entire file.

In [138]:
import urllib

def stream(n):
    i = 0
    with urllib.request.urlopen('https://02807-comp-tools.s3.us-east-2.amazonaws.com/traffic') as f:
        for line in f:
            element = line.rstrip().decode("utf-8")
            yield element
            i += 1
            if i == n:
                break

In [208]:
STREAM_SIZE = 200000
web_traffic_stream = stream(STREAM_SIZE)

In [176]:
# for i in web_traffic_stream:
#     print(i.split())

## Data structures

Hyperloglog

How many unique IPs are there in the stream?

In [177]:
import pymmh3 as mmh3
import math
import statistics

In [178]:
def Hash(string):
    return mmh3.hash(string, seed=1234)

In [179]:
def Binary(num):
    return "{0:b}".format(num)

In [180]:
def getUpper(string,m):
    if int(string) < 0:
        string=string[1:]
    return string[0:math.ceil(math.log(m,2))]

def getLower(string,m):
    if int(string) < 0:
        string=string[1:]
    return string[math.ceil(math.log(m,2)):]

In [206]:
def getPosition(string):
    count=1
    for i in string:
        if i == '1':
            return count
        count += 1
    return 0

In [182]:
def getIndex(string):
    return int(string, 2) + 1

In [183]:
def update(array, index, position):
    if index < 5:
        print(index)
    array[index]= max(array[index],position)
    return None

In [207]:
def hyperLogLog(array,element):
    # hash the element
    hashing=Hash(element)
    
    # obtain binary representation
    binary=Binary(hashing)
    print(binary)
    
    # split into upper and lower parts
    upper=getUpper(binary, 32)
    lower=getLower(binary, 32)
    
    # compute position p
    p=getPosition(lower)
    
    # obtain the index j
    j=getIndex(upper)
    
    # update array M
    update(array, j , p)
    
    return None

In [209]:
STREAM_SIZE = 200000
web_traffic_stream = stream(STREAM_SIZE)

In [210]:
M=[0]*33

In [211]:
for i in web_traffic_stream:
    IP=i.split()[0]
    hyperLogLog(M,IP)

-100101100011001001110011010011
-111010001000110101000011100001
-1100110000110101110001110
-1011100101100011010101100010010
10001101101001010100110100010
1001111011111100100010010110011
1010100010011110111100001001001
1101001010100010010110000110011
110000001010111110101011001110
-1110111111001110011100101001011
1111101000001101101101111111011
-111100011100011000100110111111
-1111110011110000011101000001111
-111000000000110010000000011100
-1001101000110001010010001110
1111100101000111110010010110111
1000110010111111100110001010001
-111001011101101101001110111011
-1111101100011110010011010000100
1111000100001100011100001011
-100101000011101101101111000110
-1000100110011101101111000011000
-111010110101110000100111001110
-1100100011110011001010000011
1110100000101101010101011101
-100010111100000000000111011010
111100110010000110110101111101
-110011100111101000110110110
1111111101111101000000110101001
-101111110011001001000100001100
111111100100110100100000111100
-1111100000001011111010010

-11010011000100101001010111110
-101111101000001010010111110101
1010011001011110001110011010001
-1000100010011011010100100101000
-1011101101101000000010001110000
1100110100001100001000001101101
-1000101110101100011110111010000
-101000001001110001000101100011
1011001010010000110101100010001
-1100110110101010110100101111101
1100000110011011101011110001111
-100110001111001011101001011100
-110001001111011111111111000110
-1101111101011110000000010001100
-1111010111110101011100101001010
1000010011111110000111100000011
-11101010110000100110001000001
-100101000111010101010001011100
100100010101001110110101111000
-11010111111001111010011101010
1010011101111110110110101010010
-1000011010110100110101001000011
-11101001110010111011100001100
-11010110000000010011101011100
1100001000001110110110111011000
-1111010111111001011000101000110
-111001100100010010011001101111
1110010001001010110100111100011
101000000010111110111000111010
1010110011001010000101010001011
110011001011101001111010010101
10110001

1111001100000110101000001011001
-1110110110000010000110111001001
-1001001110111111111011011111101
-101001110011101101000001100001
10111001100110100110100000011
1010000110010111001110011111110
-1010110101111001000011101111000
1000011011101001110111010101000
110010000110111001111100110101
-11000010001100000101000011111
10101110001001011000110011
-11000101100001001110000100000
1010111010010000110110010100111
-1000101011101111101001111111111
1110101011101011000111111111110
1001010011100101010000011101100
-11100111010001111010011000101
-1010111101000110100100011101111
-101111011000011010100001000
1101100111101001001110010000111
-111101010011010100001100111101
1111011100111101001100111011010
-1000100100111010010101011000010
1010011101111111101100111111111
-100100011000101000010110101101
1000011000101110100001111101101
-1110001101101011011001010100000
1001000010001001011010001100
110111000110011011100111100
1100101110101001110010010110010
101011100001011001010011000110
-1000011101010010101011

1000100010011000000110111001
-1100010110010100011011001101
1010011001001111001011010110100
-1101100000100000100011101011100
110111100001110001101101001110
1011000100110011100111100011001
-110000010001101101111100001011
1100111101011101110110101011000
110001010110111100011000011011
-10011110010100001000010001
-101111110011100011000010000100
-1010010010111010101111101110
-111001101001010010001000010010
100000101011111010101111000101
111110110110010000011100110
1011010011100001010000011010110
-1000011101111110010111110000
101111110101111011010101010111
-110100100001101101011101010
-10111000000110101010001110101
-1011111111001011001111101100
-1011001010010110010011011101000
1010001100010111100000001111011
-1001011011101100000101110111001
-1011010011001100110101111110110
-1011100111010110100001101010011
-100010010000000000110010100010
-10001100100001001101111000
1111100000101111111011111011000
-1101111101110101001001011011011
-1001010010100010000001001100111
-10111101100101011101000010100
-

-10100110011100101100001010011
1111101000101010110101000100000
1100100110010001001011001110011
-1011100000111000101000111111110
-11111111110111010001010001001
-101010111101000010001001010001
-1010101100010100001111110111110
-10111001010011010011101001110
1100011011001000111110110011100
-10110011000011111101101100001
-1011110011100100110010001001000
1011111000000000101011100100100
-11011100010010100010001111010
11110110010111111110111110101
1000101100011010010010110101011
-101011001010101011111101101011
1000010110011101110100110101
-1011110101110100000011000010001
-110001110101110100010110100100
-10011001010000101111011010100
-11111100011000101101101011110
-1000101001001001110110110101001
10100101001001011101110000001
1100110001000111000111010100101
1010110000001000111111
-111001100110110010011010111111
-1000011001111101000100011001000
1101101101010001101011110010000
-1101010111001110100111101001
1111010110011111011001100000101
-100101011010111100111110111110
1111001001100001011011101
-

...

-111010101011101000101001100
101001110101111101001110000001
11101011111111101111011011011
1100110010011100101100110011110
1100111000101101001001000100001
100001011010100000111100111110
10001010011000100100110001010
10110111110111111010000010110
1101011001100001001011011010100
111000111001100100001110011000
1100101011100101101001001100
-1010011111100011011011100010
1111001001001111011000010100010
1001100101100101101110100000101
11001101011010101101001100110
-10110001111011110101100100010
1010111010100000111011101111000
-111011101001100110010001011110
-111000011010010110101001111100
-100100011110110110110011100000
1000111101100100100111010111
-1110001111010001100001000000010
-1100001101101100100101100100000
1110011111100100000000101100111
111100011111000110000100010110
-1010111011100101000001000110111
-110111101011001101100001000000
11000010001011110011000101111
-111100010001101001011010110000
1000011001110101001011001001001
-1101100001100001010000010001101
-10100100100010100101100101110

-111010010100111101010100011
11011010000011110100011110010
-111011110011110010111011011011
1110000101100100011010000101110
-1011101111111111011000000001100
1111101011001110100001011001010
-110011111100110001010101010000
10001000011011111101000001
-111001001101111011101111101001
-1000111110001001010010001100011
1100001001111101010101000000001
-101000101111110100110110010010
-1100100110000111001101000101101
-11111000101001110001101111011
1111101100011100111001001011110
100101000011000111111100000100
111010011011101111011001100
1001010001111100101100011111110
110011011001110011000010100000
1101000111111010001010011010100
11111101111100001100101000111
-1100111011010000100011000110
101100110111100100000111100011
-1101101101010111001111001111
-1101000100001011110101111001011
1000000111011011100001100011000
1011010011011100111111101110010
-1000010001111101011110101101011
-1101000100000011000001101110111
-111100000001000000011011110001
1100110001010000100110011100011
11111001011111001011011000

-1111101010010000110111101001011
-1101101011000100001111000111000
-1001101111010100111011101111111
1010011000110000010000010100010
-10000110111101100011100110
111001101000010110101010110100
1011100100111000000111111101000
1010000001100010100001101101001
101111101101101001001101001011
-111010011001010110000101011110
-1010000110100110001011001100110
11110001110110001101101000110
100101010011011101100110111011
11010010111111100101110000010
1101100110111100010111101010001
1001000100010010011000101110010
1001001001100010101100101100011
-100011101111010101101011011000
1011001111000111101000001000111
100110101000001101000110001111
10100101011101100001011100
-1111011101010111111011001000001
1110101000111001010011001101011
-1001000000101010101011111011001
1000000011000110110001111010001
111000111011110101100000001
1111100010010100110000101000101
1111001100110000101000110000010
-1101100011101011100111000010011
-1000000111100000001101001010010
101011111001111100001000000101
-111000100111111101001

1110100101110100001000111100
-101101101001011100101101111000
11111101010111111101000000000
-111001011010100011100101111101
1000101100011111101100000001001
1111001100001011101011101011000
-1000000101011000001011111010001
100110110001011110011100100001
10000000111101001100001001110
1100101101100100101100100111011
1101101101010000010010110110011
1110111110101010001011111001000
101110100001110011110000100111
-1110111111011011011100111100111
111010010000011111000101100001
11011000110010110011101010001
111100010100111100100111000
10010111110011011011111001010
1101110110101100000000001000000
1111010110010100010100001010011
-110101011101010100101100100010
1001000001010100000010000110
10111011100101011011011111110
-1010100000011001101101000101101
-1111110100100000101000110000010
11001000100110110000010011
-100111010100111010010000000011
11111011111011000110100011011
111010110111001100001010111110
-1011101001011011110011000011111
-1100001111101100100100100000101
1000000000010010110110000110101
1

1011110011000111110011110001000
-1000010100010111001110101100000
-110000001000101100101111100001
1001001000011011010110000011
110010110001001110000011111010
10001100000001100001000101011
1010110011011011111110011001110
1011101011000110010100100111000
1101111010101100001111010010111
101100001011000000011100010100
110000011111010111000100010000
-111100110101111100111010100
1011111100000011011001100010100
1000110001110111100100001101
111111101110000010000010100000
110010101011000001101011001000
1001100111000100101011000001
101000011100000100101100001
101000000001010001011011000011
-1011001101111111010111111100011
-1001010000110111000101011101111
-1110001101001000101111011100100
11100100011110010001000001011
-100011110000011000100011010
-1111111011001011011101011111
10100011100001000110000110111
-1000110110000010010001010010110
-110101101100100101111000100
1100100011110111111100110101101
11011100100010011011110100111
1101011100100100011111000101011
1111111011111100100000111110
110011001010

In [205]:
M

[0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 15,
 15,
 13,
 13,
 16,
 14,
 16,
 15,
 15,
 19,
 16,
 14,
 17,
 16,
 12,
 19]

In [154]:
statistics.harmonic_mean([1,2,3,4,0])

0

In [86]:
harmonicMean(M)

ZeroDivisionError: 0.0 cannot be raised to a negative power

In [47]:
Binary(Hash32('yangyuesong'))

'-10001011111000110001111001111'

In [48]:
getUpper(Binary(Hash32('yangyuesong')),32)

'-10001'

In [49]:
getLower(Binary(Hash32('yangyuesong')),32)

'011111000110001111001111'

## Analysis